In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, AutoModelForCausalLM
import shap
import scipy as sp
import nlp
import torch

In [2]:
tokenizer = AutoTokenizer.from_pretrained("sshleifer/distilbart-xsum-12-6")
model =  AutoModelForSeq2SeqLM.from_pretrained("sshleifer/distilbart-xsum-12-6").cuda()

In [3]:
dataset = nlp.load_dataset('xsum',split='train')

WARNING - Using custom data configuration default


In [4]:
explainer = shap.Explainer(model,tokenizer)

explainers.Partition is still in an alpha state, so use with caution...


In [9]:
shap_values = explainer(dataset['document'][0:1])

In [10]:
shap.plots.text(shap_values[0])

### API

In [11]:
def f(x):
    model.eval()
    input_ids = torch.tensor([tokenizer.encode(x)]).cuda()
    with torch.no_grad():
        out=model.generate(input_ids)
    sentence = [tokenizer.decode(g, skip_special_tokens=True) for g in out][0]
    del input_ids, out
    return sentence

In [12]:
from shap.models import TeacherForcingLogits
from shap import maskers

In [13]:
wrapped_model = TeacherForcingLogits(f,text_similarity_model=model, text_similarity_tokenizer=tokenizer, device='cuda')
masker = maskers.Text(tokenizer, mask_token = "<infill>")

In [14]:
explainer_model_agnostic = shap.Explainer(wrapped_model,masker)

explainers.Partition is still in an alpha state, so use with caution...


In [15]:
shap_values_model_agnostic = explainer(dataset['document'][0:1])

In [16]:
shap.plots.text(shap_values_model_agnostic[0])